In [5]:
import numpy as np
import scipy.sparse as sp
import pandas as pd

import sys
sys.path.append('..')
import src

In [6]:
PARAMS = {
    'community': 'laurelhurst',
    'experiment_name': 'strength_of_tie',
    # resource types should be the same as the column names in the resource_preference_pmf and resource_inventory_pmf
    'resource_types': ['water', 'food', 'meds', 'transp', 'comm',
                       'faid', 'warm', 'sani', 'power', 'shelter'], 
    'tau': 5, # isolation days
    'num_scenarios': 100,
    'n': 0.78773808, # degree distribution parameter
    'p': 0.02559534, # degree distribution parameter
    'social_tie': {
        'types': ['strong', 'weak'],
        'pmf':  [0.41296, 0.58704]
    },
    'distance_decay_alpha': -1.35, # distance decay parameter
    'distances_mat': np.load('../temp/laurelhurst_distance_matrix.npy'), # distance matrix
    'sharing_preference_pmf': pd.read_csv('../temp/laurelhurst_share_pref_PMF.csv'), # sharing preference matrix
    'sharing_priority': [3, 2, 1], # sharing priorities to [strong tie, weak tie, stranger]
    'resource_inventory_pmf': pd.read_csv('../temp/laurelhurst_resource_distr_PMF.csv') # resource inventory distribution
}

In [7]:
def p2p_single_resource_sharing(resource:str, 
                                tau:float, # isolation days
                                n:float, # negative binomial distribution parameter
                                p:float, # negative binomial distribution parameter
                                distance_decay_alpha:float, # distance decay parameter
                                distance_mat:np.matrix, # distance matrix
                                sharing_preference_PMF:pd.Series, 
                                resource_inventory_PMF:pd.Series,
                                social_tie_pmf:list,
                                social_tie_types:list = ['strong', 'weak'],
                                sharing_priority:list = [3, 2, 1],
                                seed:int=0):
    """Step 1: Community-based social network construction"""
    # create a community
    community = src.Community()
    num_nodes = distance_mat.shape[0]
    community.add_nodes_from(range(num_nodes))

    # generate social ties
    np.random.seed(seed)
    degree_list = np.random.negative_binomial(n, p, size=num_nodes)
    community.generate_social_ties(degrees=degree_list, 
                                   distance_matrix=distance_mat, 
                                   distance_decay_alpha=distance_decay_alpha, 
                                   seed=seed+1)
    community.split_social_ties(types=social_tie_types, 
                                pmf=social_tie_pmf, 
                                seed=seed+2)

    """Step 2: Community-based resource-sharing network construction"""
    # generate sharing preferences
    community.generate_sharing_preference(recipient=[0, 1, 2, 3], # [nobody, strong tie only, strong and weak ties only, everybody]
                                          pmf=sharing_preference_PMF, 
                                          name=resource+'_share_preference',
                                          seed=seed+3)

    """Step 3: Community-based resource inventory"""
    community.generate_resource_inventory(support=np.arange(0, len(resource_inventory_PMF)), 
                                          pmf=resource_inventory_PMF, 
                                          name=resource, 
                                          seed=seed+4)

    # create sharing network
    share_network = community.get_share_network(sharing_preference=resource+'_share_preference', 
                                                priority=sharing_priority)

    """Step 4: Community-based P2P resource-sharing model"""
    priority_matrix = community.get_share_priority_matrix(sharing_preference=resource+'_share_preference', 
                                                          priority=sharing_priority)
    resource_inventory = [community.nodes[n][resource] for n in community.nodes]
    model = src.ResourceSharingModel(wts_matrix=priority_matrix, 
                                     inventory=resource_inventory, 
                                     isolation_days=tau)
    model.solve()

    return community, share_network, model

In [8]:
# main script for running the status quo model
for tie_prop in [[0.0, 1.0],
                 [0.1, 0.9],
                 [0.2, 0.8],
                 [0.3, 0.7],
                 [0.4, 0.6],
                 [0.5, 0.5],
                 [0.6, 0.4],
                 [0.7, 0.3],
                 [0.8, 0.2],
                 [0.9, 0.1],
                 [1.0, 0.0]]:

    for sce in range(PARAMS['num_scenarios']):
        
        # directory name for saving the results
        dir = PARAMS['community'] + '/' + PARAMS['experiment_name'] + '/tau_' + str(PARAMS['tau']) # directory name
        # Create a dataframe to store the results
        inventory_df = pd.DataFrame(columns=PARAMS['resource_types'])
        resource_df = pd.DataFrame(columns=PARAMS['resource_types'])
        
        # run the model for each resource type
        for rsc in PARAMS['resource_types']:
            community, share_network, model = p2p_single_resource_sharing(resource=rsc,
                                                                        tau=PARAMS['tau'],
                                                                        n=PARAMS['n'],
                                                                        p=PARAMS['p'],
                                                                        social_tie_types = PARAMS['social_tie']['types'],
                                                                        social_tie_pmf = tie_prop,
                                                                        distance_decay_alpha = PARAMS['distance_decay_alpha'],
                                                                        distance_mat = PARAMS['distances_mat'],
                                                                        sharing_preference_PMF = PARAMS['sharing_preference_pmf'][rsc],
                                                                        sharing_priority = PARAMS['sharing_priority'],
                                                                        resource_inventory_PMF = PARAMS['resource_inventory_pmf'][rsc],
                                                                        seed=sce)
            inventory_df[rsc] = model.inventory.flatten()
            resource_df[rsc] = model.resource.flatten()

        # save the resource inventory vector in csv file
        inventory_df.to_csv(dir + '/q_vec_tie_{}_sce_{}.csv'.format(tie_prop, sce), index=False)
        # save the final resource vector in csv file
        resource_df.to_csv(dir + '/h_vec_tie_{}_sce_{}.csv'.format(tie_prop, sce), index=False)

/Users/lzy95/Documents/GitHub/Peer-to-peer-community-sharing/results/../src/community.py:230: FutureWarning: adjacency_matrix will return a scipy.sparse array instead of a matrix in Networkx 3.0.
  return nx.adjacency_matrix(self).todense()


Gurobi Optimizer version 10.0.1 build v10.0.1rc0 (mac64[arm])

CPU model: Apple M2 Pro
Thread count: 10 physical cores, 10 logical processors, using up to 10 threads

Optimize a model with 3746 rows, 3508129 columns and 7016258 nonzeros
Model fingerprint: 0x352f7cc6
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [1e+00, 2e+00]
  Bounds range     [0e+00, 0e+00]
  RHS range        [1e+00, 5e+00]
Presolve removed 2338 rows and 3325164 columns
Presolve time: 0.82s
Presolved: 1408 rows, 182965 columns, 365921 nonzeros

Concurrent LP optimizer: primal simplex, dual simplex, and barrier
Showing barrier log only...

Ordering time: 0.00s

Barrier statistics:
 AA' NZ     : 1.377e+05
 Factor NZ  : 2.054e+05 (roughly 60 MB of memory)
 Factor Ops : 4.197e+07 (less than 1 second per iteration)
 Threads    : 8

Barrier performed 0 iterations in 1.02 seconds (1.62 work units)
Barrier solve interrupted - model solved by another algorithm


Solved with dual simplex

Use cro

/Users/lzy95/Documents/GitHub/Peer-to-peer-community-sharing/results/../src/community.py:230: FutureWarning: adjacency_matrix will return a scipy.sparse array instead of a matrix in Networkx 3.0.
  return nx.adjacency_matrix(self).todense()


Gurobi Optimizer version 10.0.1 build v10.0.1rc0 (mac64[arm])

CPU model: Apple M2 Pro
Thread count: 10 physical cores, 10 logical processors, using up to 10 threads

Optimize a model with 3746 rows, 3508129 columns and 7016258 nonzeros
Model fingerprint: 0xa4829fb9
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [1e+00, 2e+00]
  Bounds range     [0e+00, 0e+00]
  RHS range        [1e+00, 5e+00]
Presolve removed 2478 rows and 3329603 columns
Presolve time: 0.85s
Presolved: 1268 rows, 178526 columns, 357035 nonzeros

Concurrent LP optimizer: primal simplex, dual simplex, and barrier
Showing barrier log only...

Ordering time: 0.00s

Barrier statistics:
 AA' NZ     : 1.367e+05
 Factor NZ  : 2.414e+05 (roughly 60 MB of memory)
 Factor Ops : 6.706e+07 (less than 1 second per iteration)
 Threads    : 8

Barrier performed 0 iterations in 1.05 seconds (1.86 work units)
Barrier solve interrupted - model solved by another algorithm


Solved with dual simplex

Use cro

/Users/lzy95/Documents/GitHub/Peer-to-peer-community-sharing/results/../src/community.py:230: FutureWarning: adjacency_matrix will return a scipy.sparse array instead of a matrix in Networkx 3.0.
  return nx.adjacency_matrix(self).todense()


...

Gurobi Optimizer version 10.0.1 build v10.0.1rc0 (mac64[arm])

CPU model: Apple M2 Pro
Thread count: 10 physical cores, 10 logical processors, using up to 10 threads

Optimize a model with 3746 rows, 3508129 columns and 7016258 nonzeros
Model fingerprint: 0x360a6a37
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [1e+00, 3e+00]
  Bounds range     [0e+00, 0e+00]
  RHS range        [1e+00, 5e+00]
Presolve removed 2408 rows and 3314518 columns
Presolve time: 0.94s
Presolved: 1338 rows, 193611 columns, 387142 nonzeros

Concurrent LP optimizer: primal simplex, dual simplex, and barrier
Showing barrier log only...

Ordering time: 0.00s

Barrier statistics:
 AA' NZ     : 1.488e+05
 Factor NZ  : 2.684e+05 (roughly 60 MB of memory)
 Factor Ops : 8.073e+07 (less than 1 second per iteration)
 Threads    : 8

Barrier performed 0 iterations in 1.23 seconds (2.02 work units)
Barrier solve interrupted - model solved by another algorithm


Solved with primal simplex
Iterat

/Users/lzy95/Documents/GitHub/Peer-to-peer-community-sharing/results/../src/community.py:230: FutureWarning: adjacency_matrix will return a scipy.sparse array instead of a matrix in Networkx 3.0.
  return nx.adjacency_matrix(self).todense()


Gurobi Optimizer version 10.0.1 build v10.0.1rc0 (mac64[arm])

CPU model: Apple M2 Pro
Thread count: 10 physical cores, 10 logical processors, using up to 10 threads

Optimize a model with 3746 rows, 3508129 columns and 7016258 nonzeros
Model fingerprint: 0xc2120bf9
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [1e+00, 3e+00]
  Bounds range     [0e+00, 0e+00]
  RHS range        [1e+00, 5e+00]
Presolve removed 2274 rows and 3289100 columns
Presolve time: 1.03s
Presolved: 1472 rows, 219029 columns, 438004 nonzeros

Concurrent LP optimizer: primal simplex, dual simplex, and barrier
Showing barrier log only...

Ordering time: 0.00s

Barrier performed 0 iterations in 1.29 seconds (2.04 work units)
Barrier solve interrupted - model solved by another algorithm


Solved with primal simplex
Iteration    Objective       Primal Inf.    Dual Inf.      Time
    1584    2.2750000e+03   0.000000e+00   0.000000e+00      1s

Use crossover to convert LP symmetric solution 

/Users/lzy95/Documents/GitHub/Peer-to-peer-community-sharing/results/../src/community.py:230: FutureWarning: adjacency_matrix will return a scipy.sparse array instead of a matrix in Networkx 3.0.
  return nx.adjacency_matrix(self).todense()


Gurobi Optimizer version 10.0.1 build v10.0.1rc0 (mac64[arm])

CPU model: Apple M2 Pro
Thread count: 10 physical cores, 10 logical processors, using up to 10 threads

Optimize a model with 3746 rows, 3508129 columns and 7016258 nonzeros
Model fingerprint: 0xff076c4a
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [1e+00, 3e+00]
  Bounds range     [0e+00, 0e+00]
  RHS range        [1e+00, 5e+00]
Presolve removed 2385 rows and 3307153 columns
Presolve time: 1.21s
Presolved: 1361 rows, 200976 columns, 401866 nonzeros

Concurrent LP optimizer: primal simplex, dual simplex, and barrier
Showing barrier log only...

Ordering time: 0.00s

Barrier statistics:
 AA' NZ     : 2.009e+05
 Factor NZ  : 3.755e+05 (roughly 80 MB of memory)
 Factor Ops : 1.400e+08 (less than 1 second per iteration)
 Threads    : 8

                  Objective                Residual
Iter       Primal          Dual         Primal    Dual     Compl     Time
   0   5.47477580e+05  2.77571794e+0